## やっていること
* 単独測位結果の事後処理
* 1つのcollectionで複数のphoneを使用している場合に平均値を使用する
* 止まっているところを検出⇛平均値を採用する

### TODO
* 1測位ごとに誤差を推定してmixしたい

In [116]:
using DataFrames
using DataFramesMeta
using CategoricalArrays
using Pipe
using JLD2
using Dates
using LeapSeconds
using Combinatorics
using Random
using Statistics
using Profile
using ProgressMeter
using Format
# using Base.Threads
using CSV
using Glob
using Formatting
using DelimitedFiles
using TextAnalysis
using BenchmarkTools
using GeographicLib
using LinearAlgebra
using LsqFit
using PyCall
using OpenStreetMapX
flm = pyimport("folium")

ENV["COLUMNS"]=1700;
ENV["LINES"]=10;
F = Float64
S = Symbol

using PyPlot
rcParams = PyPlot.PyDict(PyPlot.matplotlib."rcParams")
rcParams["font.size"] = 6
rcParams["figure.figsize"] = [9,9]
rcParams["figure.dpi"] = 220
plt.style.use("seaborn-darkgrid");

include("../src/util_fc.jl")

Main.util_fc

In [117]:
@load "../DataFrames/train_df_concat_31.jdl2" train_df_concat
@load "../DataFrames/test_df_concat_31.jdl2" test_df_concat

1-element Array{Symbol,1}:
 :test_df_concat

In [118]:
util_fc.XY2acce(train_df_concat, :X_obs_rjct_outlier_klmn, :Y_obs_rjct_outlier_klmn)
util_fc.XY2acce(test_df_concat, :X_obs_rjct_outlier_klmn, :Y_obs_rjct_outlier_klmn)

In [119]:
train_df_concat[!, :weight] = 1 ./ (train_df_concat[!, :Ax_X_obs_rjct_outlier_klmn].^2 + train_df_concat[!, :Ay_Y_obs_rjct_outlier_klmn].^2);
train_df_concat[isnan.(train_df_concat.weight), :weight] .= 0.1
train_df_concat[isinf.(train_df_concat.weight), :weight] .= 0.1
test_df_concat[!, :weight] = 1 ./ (test_df_concat[!, :Ax_X_obs_rjct_outlier_klmn].^2 + test_df_concat[!, :Ay_Y_obs_rjct_outlier_klmn].^2);
test_df_concat[isnan.(test_df_concat.weight), :weight] .= 0.1
test_df_concat[isinf.(test_df_concat.weight), :weight] .= 0.1

39-element view(::Array{Float64,1}, [1, 3489, 7006, 9261, 9262, 11688, 14006, 16314, 21169, 26196  …  67909, 67910, 68933, 74068, 76392, 82254, 83961, 87447, 89425, 89426]) with eltype Float64:
 0.1
 0.1
 0.1
 ⋮
 0.1
 0.1

In [122]:
util_fc.mix_pos(train_df_concat, :X_obs_rjct_outlier_klmn, :Y_obs_rjct_outlier_klmn, :weight)
util_fc.mix_pos(test_df_concat, :X_obs_rjct_outlier_klmn, :Y_obs_rjct_outlier_klmn, :weight)
util_fc.XY2lnglat(train_df_concat, :X_obs_rjct_outlier_klmn_mix, :Y_obs_rjct_outlier_klmn_mix)
util_fc.calc_score(train_df_concat, :lngDeg_X_obs_rjct_outlier_klmn_mix,:latDeg_Y_obs_rjct_outlier_klmn_mix)
util_fc.mix_pos(test_df_concat, :X_obs_rjct_outlier_klmn, :Y_obs_rjct_outlier_klmn, :weight)
util_fc.mix_pos(test_df_concat, :X_obs_rjct_outlier_klmn, :Y_obs_rjct_outlier_klmn, :weight)
util_fc.XY2lnglat(test_df_concat, :X_obs_rjct_outlier_klmn_mix, :Y_obs_rjct_outlier_klmn_mix)

In [123]:
# X * Wx + Y * Wy / (Wx + Wy)
function var_a(a::Vector{Union{Missing, F}}, n::Int)::Vector{F}
    Va = similar(a, Union{F, Missing})
    Va[1:n] .= -0.1
    for i in n+1:length(a)
        Va[i] = var(a[i-n:i]) |> sqrt
    end
    mask = ismissing.(Va)
    Va[mask] .= -0.1
    return F.(Va)
end

function detect_stoping(df::DataFrame, line::F, lng::S, lat::S)
    df[!, :Accel_lowpass] =  sqrt.(df.AccelXMps2_lowpass.^2 + df.AccelYMps2_lowpass .^2  + df.AccelZMps2_lowpass.^2)
    df[!, S("$(lng)_stop_mean")] = similar(df[!, lng], F)
    df[!, S("$(lat)_stop_mean")] = similar(df[!, lat], F)
    gd = groupby(df, :phone)
    for gdf in gd
        lng_arr = F[]
        lat_arr = F[]
        idx = Int[]
        lng_result = similar(gdf[:, lng],F)
        lat_result = similar(gdf[:, lat],F)
        a = gdf.Accel_lowpass |> Array
        Va = var_a(a, 4)
        for (i, (lng_f, lat_f)) in enumerate(zip(gdf[:, lng], gdf[:, lat]))
            if (abs(Va[i]) < line)  & (~occursin("Mi", gdf.phone[1]))
                push!(lng_arr, lng_f)
                push!(lat_arr, lat_f)
                push!(idx, i)
            elseif length(idx) > 0
                lng_result[idx] .= mean(lng_arr)
                lat_result[idx] .= mean(lat_arr)
                idx = Int[]
                lng_arr = F[]
                lat_arr = F[]
                lng_result[i] = lng_f
                lat_result[i] = lat_f
            else
                lng_result[i] =lng_f
                lat_result[i] =lat_f
            end
        end
        gdf[:, S("$(lng)_stop_mean")] = lng_result
        gdf[:, S("$(lat)_stop_mean")] = lat_result
    end
end
detect_stoping(train_df_concat, 0.004, :X_obs_rjct_outlier_klmn_mix, :Y_obs_rjct_outlier_klmn_mix)
detect_stoping(test_df_concat, 0.004, :X_obs_rjct_outlier_klmn_mix, :Y_obs_rjct_outlier_klmn_mix)#

In [127]:
test_df_concat.weight |> maximum

4.524470389714522e17

In [126]:
isnan.(train_df_concat.latDeg_Y_obs_rjct_outlier_klmn_mix) |> sum
test.weight .|> isinf |> sum

LoadError: [91mUndefVarError: test not defined[39m

In [128]:
util_fc.XY2lnglat(train_df_concat, :X_obs_rjct_outlier_klmn_mix_stop_mean,:Y_obs_rjct_outlier_klmn_mix_stop_mean)
util_fc.calc_score(train_df_concat, :lngDeg_X_obs_rjct_outlier_klmn_mix_stop_mean, :latDeg_Y_obs_rjct_outlier_klmn_mix_stop_mean)

util_fc.XY2lnglat(test_df_concat, :X_obs_rjct_outlier_klmn_mix_stop_mean,:Y_obs_rjct_outlier_klmn_mix_stop_mean)

In [129]:
@save "../DataFrames/train_df_concat_40.jdl2" train_df_concat
@save "../DataFrames/test_df_concat_40.jdl2" test_df_concat
# @save "../DataFrames/score_df_40.jdl2" score_df 

In [131]:
util_fc.write_sub(test_df_concat, :lngDeg_X_obs_rjct_outlier_klmn_mix_stop_mean, :latDeg_Y_obs_rjct_outlier_klmn_mix_stop_mean, "sub12.csv")

IOStream(<file ../submit/sub12.csv>)

In [17]:
df = CSV.read("../submit/sub08.csv", DataFrame)
flm = pyimport("folium")
matplotlib_cm = pyimport("matplotlib.cm")
matplotlib_colors = pyimport("matplotlib.colors")
cmap = matplotlib_cm.get_cmap("prism")

map_data = get_map_data("/home/yuri/work/OpenStreetMap/planet_-122.596,37.414_-121.795,37.817.osm", use_cache=true);

┌ Info: Read map data from cache /home/yuri/work/OpenStreetMap/planet_-122.596,37.414_-121.795,37.817.osm.cache
└ @ OpenStreetMapX /home/yuri/.julia/packages/OpenStreetMapX/pfbvr/src/parseMap.jl:98


In [30]:
@orderby(score_df,:score .*(-1))

73×4 DataFrame
 Row │ phone                              score     kl_d50    kl_d95   
     │ String                             Float64   Float64   Float64  
─────┼─────────────────────────────────────────────────────────────────
   1 │ 2021-04-22-US-SJC-1_SamsungS20Ul…  15.2421   6.73767   23.7465
   2 │ 2021-04-22-US-SJC-1_Pixel4         14.973    7.01812   22.9279
   3 │ 2021-04-28-US-SJC-1_Pixel4         13.9584   4.51519   23.4015
   4 │ 2021-04-28-US-SJC-1_SamsungS20Ul…  13.7836   4.59398   22.9731
   5 │ 2021-04-29-US-SJC-2_SamsungS20Ul…  13.7706   4.39065   23.1506
   6 │ 2021-04-29-US-SJC-2_Pixel4         13.6186   4.37503   22.8622
   7 │ 2021-04-29-US-MTV-1_SamsungS20Ul…   7.44593  4.86389   10.028
   8 │ 2021-04-29-US-MTV-1_Pixel5          7.4291   5.07337    9.78483
   9 │ 2021-04-29-US-MTV-1_Pixel4          7.37283  5.01565    9.73001
  10 │ 2021-03-10-US-SVL-1_SamsungS20Ul…   4.95779  2.88596    7.02963
  11 │ 2021-03-10-US-SVL-1_Pixel4XL        4.91719  2.94678    6.8876
  ⋮  │                 ⋮                     ⋮         ⋮         ⋮
  64 │ 2020-05-14-US-MTV-1_Pixel4          2.24208  1.50684    2.97732
  65 │ 2020-05-21-US-MTV-2_Pixel4XL        2.2169   0.862011   3.57179
  66 │ 2020-05-14-US-MTV-1_Pixel4XLModd…   2.18384  1.41645    2.95123
  67 │ 2020-05-14-US-MTV-2_Pixel4          2.15522  1.34355    2.96688
  68 │ 2020-07-08-US-MTV-1_Pixel4XLModd…   2.09352  0.883032   3.30401
  69 │ 2020-06-04-US-MTV-1_Pixel4          2.07638  1.17014    2.98262
  70 │ 2020-06-04-US-MTV-1_Pixel4XL        2.06814  1.21313    2.92314
  71 │ 2020-06-05-US-MTV-1_Pixel4XL        2.04645  0.986058   3.10683
  72 │ 2020-07-08-US-MTV-1_Pixel4XL        1.94657  0.96572    2.92742
  73 │ 2020-06-05-US-MTV-1_Pixel4          1.94254  0.961889   2.9232
                                                        52 rows omitted

In [34]:
gd= groupby(train_df_concat, :phone)
m = flm.Map()
for gdf in gd
    score = score_df[score_df.phone .== gdf.phone[1], :score][1]
    if score < 10.0
        continue
    end
    obs = [(x, y) for (x,y) in zip(gdf.latDeg, gdf.lngDeg)]
    gt = [(x, y) for (x,y) in zip(gdf.gt_latDeg, gdf.gt_lngDeg)]
    info = "phone: $(gdf.phone[1])\n<br>" *
        "score: $(score)"
    flm.PolyLine(obs, color="red",
        popup=info).add_to(m)
    flm.PolyLine(gt, color="blue"
        ).add_to(m)
end

gd = groupby(df, :phone)
for gdf in gd
    obs = [(x, y) for (x,y) in zip(gdf.latDeg, gdf.lngDeg)]
    info = "phone: $(gdf.phone[1])\n<br>" *
        "score: $(score)"
    flm.PolyLine(obs, color="orange",
        popup=info).add_to(m)
end

MAP_BOUNDS = [(map_data.bounds.min_y,map_data.bounds.min_x),(map_data.bounds.max_y,map_data.bounds.max_x)]
flm.Rectangle(MAP_BOUNDS, color="black",weight=6).add_to(m)
m.fit_bounds(MAP_BOUNDS)
m

PyObject <folium.folium.Map object at 0x7fb19d5282e8>

In [22]:
test_df_concat

91486×32 DataFrame
   Row │ collectionName       phoneName        millisSinceGpsEpoch  latDeg   lngDeg    heightAboveWgs84EllipsoidM  phone                              time_UTC                 UncalAccelXMps2  UncalAccelYMps2  UncalAccelZMps2  UncalGyroXRadPerSec  UncalGyroYRadPerSec  UncalGyroZRadPerSec  yawDeg     rollDeg    pitchDeg   X_obs      Y_obs      lngDeg_centre  latDeg_centre  acce1_fm_obs  acce2_fm_obs  X_obs_outlier  Y_obs_outlier  X_klmn     Y_klmn     kl_lngDeg  kl_latDeg  lng_mix   lat_mix  count   
       │ String               String           Int64                Float64  Float64   Float64                     String                             DateTime                 Float64?         Float64?         Float64?         Float64?             Float64?             Float64?             Float64?   Float64?   Float64?   Float64    Float64    Float64        Float64        Float64       Float64       Float64        Float64        Float64    Float64    Float64    Float64    Float64   Float64  Float64 
───────┼───────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────
     1 │ 2020-05-15-US-MTV-1  Pixel4                 1273608785432  37.4166  -122.082                      -30.69  2020-05-15-US-MTV-1_Pixel4         2020-05-15T20:12:47.432        -0.791842          9.58733        -0.289955         -0.0431192            0.00375824          -0.0185779    missing    missing    missing    10117.8    -3791.66        -122.196        37.4508      1.66349       4.35059       10117.8        -3791.66   10117.5    -3791.1     -122.082    37.4166  -122.082  37.4166      2.0
     2 │ 2020-05-15-US-MTV-1  Pixel4                 1273608786432  37.4166  -122.082                      -31.76  2020-05-15-US-MTV-1_Pixel4         2020-05-15T20:12:48.432        -0.763506          9.95471        -0.792142         -0.0198911            0.00478713          -0.0151043    missing    missing    missing    10119.0    -3789.66        -122.196        37.4508      1.66349       4.35059       10119.0        -3789.66   10117.7    -3791.01    -122.082    37.4166  -122.082  37.4166      2.0
     3 │ 2020-05-15-US-MTV-1  Pixel4                 1273608787432  37.4167  -122.082                      -31.65  2020-05-15-US-MTV-1_Pixel4         2020-05-15T20:12:49.432        -0.638176         10.0949         -0.91052           0.0117501            0.000798079         -0.0128892    missing    missing    missing    10119.1    -3788.95        -122.196        37.4508      6.17252       4.35059       10119.1        -3788.95   10117.7    -3791.12    -122.082    37.4166  -122.082  37.4166      2.0
     4 │ 2020-05-15-US-MTV-1  Pixel4                 1273608788432  37.4166  -122.082                      -31.52  2020-05-15-US-MTV-1_Pixel4         2020-05-15T20:12:50.432        -0.600274         10.179          -1.05559           0.00968074           0.00160048          -0.0161357    missing    missing    missing    10116.9    -3793.98        -122.196        37.4508      5.36328       1.80193       10116.9        -3793.98   10118.1    -3791.82    -122.082    37.4166  -122.082  37.4166      2.0
     5 │ 2020-05-15-US-MTV-1  Pixel4                 1273608789432  37.4166  -122.082                      -28.95  2020-05-15-US-MTV-1_Pixel4         2020-05-15T20:12:51.432        -0.639362          9.70407        -1.5016           -0.00309449          -0.00890918          -0.0151488    missing    missing    missing    10116.1    -3793.8         -122.196        37.4508      1.07889       4.81736       10116.1        -3793.8    10117.9    -3791.85    -1